In [ ]:
from google.colab import files
uploaded= files.upload()

Saving training.1600000.processed.noemoticon.csv.zip to training.1600000.processed.noemoticon.csv (2).zip


In [ ]:
import pandas as pd
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from gensim import corpora, models

nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')
nltk.download('punkt_tab')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


True

In [ ]:
# Example: Sentiment140 tweets
df = pd.read_csv('training.1600000.processed.noemoticon.csv.zip',
                 encoding='latin-1',
                 names=['target', 'ids', 'date', 'flag', 'user', 'text'])

# Keep a smaller sample for faster testing
df = df[['text']].sample(5000, random_state=42)
print(df.head(3))


                                                     text
541200             @chrishasboobs AHHH I HOPE YOUR OK!!! 
750     @misstoriblack cool , i have no tweet apps  fo...
766711  @TiannaChaos i know  just family drama. its la...


In [ ]:
stop_words = set(stopwords.words('english'))
lemmatizer = WordNetLemmatizer()

def preprocess(text):
    tokens = word_tokenize(text.lower())
    tokens = [w for w in tokens if w.isalpha()]  # Remove punctuation/numbers
    tokens = [w for w in tokens if w not in stop_words]
    tokens = [lemmatizer.lemmatize(w) for w in tokens]
    return tokens

df['tokens'] = df['text'].apply(preprocess)
print(df['tokens'].head(3))


541200                      [chrishasboobs, ahhh, hope, ok]
750                [misstoriblack, cool, tweet, apps, razr]
766711    [tiannachaos, know, family, drama, next, time,...
Name: tokens, dtype: object


In [ ]:
# Create a dictionary and corpus for Gensim LDA
dictionary = corpora.Dictionary(df['tokens'])
corpus = [dictionary.doc2bow(tokens) for tokens in df['tokens']]

print("Sample bag-of-words for first doc:", corpus[0])


Sample bag-of-words for first doc: [(0, 1), (1, 1), (2, 1), (3, 1)]


In [ ]:
# Train LDA model
lda_model = models.LdaModel(corpus=corpus,
                            id2word=dictionary,
                            num_topics=5,   # you can tune this
                            passes=10,
                            random_state=42)

# Show topics
topics = lda_model.print_topics(num_words=5)
for topic in topics:
    print(topic)


(0, '0.009*"sad" + 0.008*"http" + 0.008*"want" + 0.007*"go" + 0.007*"get"')
(1, '0.016*"day" + 0.009*"work" + 0.008*"get" + 0.008*"go" + 0.007*"today"')
(2, '0.022*"quot" + 0.015*"na" + 0.010*"get" + 0.009*"lol" + 0.008*"gon"')
(3, '0.020*"good" + 0.010*"really" + 0.010*"u" + 0.009*"got" + 0.008*"like"')
(4, '0.009*"going" + 0.007*"great" + 0.007*"day" + 0.007*"want" + 0.006*"quot"')


In [ ]:
# Example: get dominant topic for each tweet
def get_topic(doc_bow):
    topics = lda_model.get_document_topics(doc_bow)
    topics = sorted(topics, key=lambda x: -x[1])
    return topics[0][0] if topics else None

df['topic'] = [get_topic(bow) for bow in corpus]
print(df[['text', 'topic']].head(10))


                                                      text  topic
541200              @chrishasboobs AHHH I HOPE YOUR OK!!!       1
750      @misstoriblack cool , i have no tweet apps  fo...      3
766711   @TiannaChaos i know  just family drama. its la...      1
285055   School email won't open  and I have geography ...      3
705995                              upper airways problem       0
379611          Going to miss Pastor's sermon on Faith...       1
1189018            on lunch....dj should come eat with me       0
667030    @piginthepoke oh why are you feeling like that?       3
93541      gahh noo!peyton needs to live!this is horrible       2
1097326  @mrstessyman thank you glad you like it! There...      1
